In [19]:
import numpy as np
import openai
import pandas as pd
import os
import sys
import time

# Add the path to the constants file to the system path
sys.path.append('../../../')
from constants import *
from evaluation_utils import *
from path_utils import *
from ChatCompletion_OpenAI_API import *

# OpenAI API Key
openai.api_key = OPENAI_API_KEY

In [20]:
# source code folder path
rec_sys_dir = get_rec_sys_directory()
print(f"Rec-sys directory: {rec_sys_dir}")

# data folder path
DATA_DIR = os.path.join(rec_sys_dir, '../data')
print(f"Data directory: {DATA_DIR}")

# data path
data_path = os.path.join(DATA_DIR, 'ml-1m/merged_data.dat')
print(f'Data path: {data_path}')

# output
ZERO_SHOT_SAVE_PATH = os.path.join(DATA_DIR, 'ml-1m/output/title_zero_shot.dat')
print(f'Data path: {ZERO_SHOT_SAVE_PATH}')

ZERO_SHOT_RERUN_PATH = os.path.join(DATA_DIR, 'ml-1m/output/rerun_title_zero_shot.dat')
print(f'Data path: {ZERO_SHOT_RERUN_PATH}')

# few shot save path
FEW_SHOT_1_OBS_SAVE_PATH = os.path.join(DATA_DIR, 'ml-1m/output/title_1_test_predictions_few_shot.csv')
print(f'Few shot save path: {FEW_SHOT_1_OBS_SAVE_PATH}')


# few shot save path
FEW_SHOT_1_OBS_RERUN_PATH = os.path.join(DATA_DIR, 'ml-1m/output/title_1_test_predictions_few_shot.csv')
print(f'Few shot save path: {FEW_SHOT_1_OBS_SAVE_PATH}')

Rec-sys directory: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook
Data directory: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data
Data path: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/merged_data.dat
Data path: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/output/title_zero_shot.dat
Data path: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/output/rerun_title_zero_shot.dat
Few shot save path: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/output/title_1_test_predictions_few_shot.csv
Few shot save path: /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/output/title_1_test_predictions_few_shot.csv


# Data Overview

In [21]:

# Read the data
data = pd.read_csv(data_path)

# get statistic and first few data of NUM_SAMPLES rows
data.info()
data.head(NUM_EXAMPLES)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000209 entries, 0 to 1000208
Data columns (total 10 columns):
 #   Column      Non-Null Count    Dtype 
---  ------      --------------    ----- 
 0   UserID      1000209 non-null  int64 
 1   MovieID     1000209 non-null  int64 
 2   Rating      1000209 non-null  int64 
 3   Timestamp   1000209 non-null  int64 
 4   Gender      1000209 non-null  object
 5   Age         1000209 non-null  int64 
 6   Occupation  1000209 non-null  int64 
 7   Zip-code    1000209 non-null  object
 8   Title       1000209 non-null  object
 9   Genres      1000209 non-null  object
dtypes: int64(6), object(4)
memory usage: 76.3+ MB


UserID  MovieID  Rating  Timestamp Gender  Age  Occupation Zip-code  \
0       1     1193       5  978300760      F    1          10    48067   
1       2     1193       5  978298413      M   56          16    70072   
2      12     1193       4  978220179      M   25          12    32793   
3      15     1193       4  978199279      M   25           7    22903   
4      17     1193       5  978158471      M   50           1    95350   

                                    Title Genres  
0  One Flew Over the Cuckoo's Nest (1975)  Drama  
1  One Flew Over the Cuckoo's Nest (1975)  Drama  
2  One Flew Over the Cuckoo's Nest (1975)  Drama  
3  One Flew Over the Cuckoo's Nest (1975)  Drama  
4  One Flew Over the Cuckoo's Nest (1975)  Drama

# Zero-shot (OpenAI API)

In [17]:
import re

def extract_numeric_rating(rating_text):
    """
    Extract numeric rating from response text.

    Args:
        rating_text (str): Text containing numeric rating.

    Returns:
        float: Extracted rating value. Returns 0 for unexpected responses.
    """
    try:
        # Updated regex to capture ratings in sentences
        # Looks for a number followed by the word 'stars' or a percentage sign
        rating_match = re.search(r'\b(\d+(\.\d+)?)\s*(stars|%)\b', rating_text)
        if rating_match:
            rating = float(rating_match.group(1))
            if 1 <= rating <= 5:
                return rating
            else:
                print(f"Rating out of expected range (1-5): {rating_text}")
                return 0
        else:
            print(f"No valid rating found in the response: {rating_text}")
            return 0
    except Exception as e:
        print(f"Error extracting rating: {e}. Full response: {rating_text}")
        return 0

# Example usage
print(extract_numeric_rating('API call response: "The user will rate "Carrie (1976)" as 4 stars, 85%."'))



def predict_ratings_zero_shot_and_save(data,
                                       columns_for_prediction=['title'],
                                       user_column_name='reviewerID',
                                       title_column_name='title',
                                       asin_column_name='asin',
                                       rating_column_name='rating',
                                       pause_every_n_users=PAUSE_EVERY_N_USERS,
                                       sleep_time=SLEEP_TIME,
                                       save_path='zero_shot_predictions.csv',
                                       seed=RANDOM_STATE):
    """
    Predicts a single random rating per user using a zero-shot approach and saves the predictions to a CSV file.

    Parameters:
    - data (DataFrame): Dataset containing user ratings.
    - columns_for_prediction (list of str): Columns to use for prediction.
    - user_column_name (str): Column name for user IDs.
    - title_column_name (str): Column name for item titles.
    - asin_column_name (str): Column name for item IDs.
    - rating_column_name (str): Column name for actual ratings.
    - pause_every_n_users (int): Number of users to process before pausing.
    - sleep_time (int): Sleep time in seconds during pause.
    - save_path (str): Path to save the predictions CSV file.
    - seed (int): Seed for random number generation.

    Returns:
    - DataFrame: DataFrame containing prediction results.
    """

    results = []
    random.seed(seed)

    # Group data by user and filter users with at least 5 records
    grouped_data = data.groupby(user_column_name).filter(lambda x: len(x) >= 5)
    unique_users = grouped_data[user_column_name].unique()

    for i, user_id in enumerate(unique_users):
        user_data = grouped_data[grouped_data[user_column_name] == user_id]
        # Select a random record for each user
        random_row = user_data.sample(n=1, random_state=seed).iloc[0]

        # Generate combined text for prediction using specified columns
        combined_text = ' | '.join([f"{col}: {random_row[col]}" for col in columns_for_prediction])

        # Predict rating using zero-shot approach
        predicted_rating = predict_rating_combined_ChatCompletion(combined_text, approach="zero-shot")
        item_id = random_row[asin_column_name]
        actual_rating = random_row[rating_column_name]
        title = random_row[title_column_name]

        results.append([user_id, item_id, title, actual_rating, predicted_rating])

        # Print progress and pause if necessary
        if (i + 1) % pause_every_n_users == 0:
            print(f"Processed {i + 1} users. Pausing for {sleep_time} seconds...")
            time.sleep(sleep_time)

    # Save results to CSV
    results_df = pd.DataFrame(results, columns=['user_id', 'item_id', 'title', 'actual_rating', 'predicted_rating'])
    results_df.to_csv(save_path, index=False)
    print(f"Predictions saved to {save_path}")

    return results_df


4.0


In [10]:
%%time

predict_ratings_zero_shot_and_save(data,
                                       columns_for_prediction=['Title'],
                                       user_column_name='UserID',
                                       title_column_name='Title',
                                       asin_column_name='MovieID',
                                       rating_column_name='Rating',
                                       pause_every_n_users=PAUSE_EVERY_N_USERS,
                                       sleep_time=SLEEP_TIME,
                                       save_path=ZERO_SHOT_SAVE_PATH)

Constructed Prompt for zero-shot approach:

The prompt:
**********
How will user rate this Title: Pleasantville (1998)? (1 being lowest and 5 being highest) Attention! Just give me back the exact number as a result, and you don't need a lot of text.

Based on the above information, please predict user's rating for the product: (1 being lowest and 5 being highest, The output should be like: (x stars, xx%), do not explain the reason.)
**********

Unexpected Error: Error communicating with OpenAI: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
Constructed Prompt for zero-shot approach:

The prompt:
**********
How will user rate this Title: GoodFellas (1990)? (1 being lowest and 5 being highest) Attention! Just give me back the exact number as a result, and you don't need a lot of text.

Based on the above information, please predict user's rating for the product: (1 being lowest and 5 being highest, The output should be like: (x stars, xx%), d

user_id  item_id                                              title  \
0           1     2321                               Pleasantville (1998)   
1           2     1213                                  GoodFellas (1990)   
2          12     1233                        Boat, The (Das Boot) (1981)   
3          15     2997                        Being John Malkovich (1999)   
4          17     2762                            Sixth Sense, The (1999)   
...       ...      ...                                                ...   
6035     3537     3718                               American Pimp (1999)   
6036     2908     1261                 Evil Dead II (Dead By Dawn) (1987)   
6037     2982      177                           Lord of Illusions (1995)   
6038     3893     3822  Girl on the Bridge, The (La Fille sur le Pont)...   
6039     4211     3834                                Bronco Billy (1980)   

      actual_rating                                   predicted_rating  
0                 3  (None, Error communicating with OpenAI: ('Conn...  
1                 2                                                4.0  
2                 3                                                4.0  
3                 2                                                4.0  
4                 5                                                4.0  
...             ...                                                ...  
6035              1                                                4.0  
6036              5                                                4.0  
6037              1                                                3.0  
6038              4                                                4.0  
6039              2                                                4.0  

[6040 rows x 5 columns]

In [11]:

# Read the data
data = pd.read_csv(ZERO_SHOT_SAVE_PATH)

# Display the original data types
# print("Original Data Types:")
# print(data.dtypes)
# print("\n")

# Attempt to convert ratings to float and add a flag for conversion failure
data['is_rating_float'] = pd.to_numeric(data['predicted_rating'], errors='coerce').notna()

# Filter rows where ratings are not float
non_float_ratings = data[data['is_rating_float'] == False]

# Number of rows with non-float ratings
print(f"Number of rows with non-float ratings: {len(non_float_ratings)}")

# Display rows with non-float ratings
print("Rows with non-float ratings:")
non_float_ratings.head(3)


Number of rows with non-float ratings: 43
Rows with non-float ratings:


user_id  item_id                           title  actual_rating  \
0           1     2321            Pleasantville (1998)              3   
2124     1883     1358              Sling Blade (1996)              4   
2341      237     2150  Gods Must Be Crazy, The (1980)              4   

                                       predicted_rating  is_rating_float  
0     (None, "Error communicating with OpenAI: ('Con...            False  
2124  (None, 'The server had an error while processi...            False  
2341  (None, 'The server is overloaded or not ready ...            False

In [12]:
%%time

data = pd.read_csv(ZERO_SHOT_SAVE_PATH)

# Rerun predictions for failed cases and save the updated data
rerun_save_path = os.path.join(DATA_DIR, 'movie-ml-latest-small/output/rerun_title_large_predictions_zero_shot.csv')
columns_for_prediction = ['title']
updated_data = rerun_failed_zero_shot_predictions(data, ZERO_SHOT_SAVE_PATH, rerun_save_path, columns_for_prediction, PAUSE_EVERY_N_USERS, SLEEP_TIME)

# Remove rows with non-float ratings and save the cleaned data
cleaned_data = updated_data[pd.to_numeric(updated_data['predicted_rating'], errors='coerce').notna()]
cleaned_data.to_csv(ZERO_SHOT_SAVE_PATH, index=False)

# Evaluate the model predictions
evaluate_model_predictions_rmse_mae(ZERO_SHOT_SAVE_PATH, NUM_EXAMPLES, 'actual_rating', 'predicted_rating')


Re-running predictions for 43 failed cases.
Predictions saved to /Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/movie-ml-latest-small/output/rerun_title_large_predictions_zero_shot.csv
RMSE: 1.5640 (95% CI: (1.5259, 1.6036)) ± 0.0004
MAE: 1.0816 (95% CI: (1.0529, 1.1109)) ± 0.0003

First few actual vs predicted ratings:
Actual: 2, Predicted: 4.0000
Actual: 3, Predicted: 4.0000
Actual: 2, Predicted: 4.0000
Actual: 5, Predicted: 4.0000
Actual: 1, Predicted: 3.0000
CPU times: user 26.2 s, sys: 13.7 ms, total: 26.3 s
Wall time: 26.4 s


# Few-shot (OpenAI API)


+ For each user, we'll use 4 of their ratings as training data to predict ratings for the rest of their products. Finally, we'll evaluate the predictions against the actual ratings to calculate the overall RMSE and MAE.

+ The rating_history_str now includes both the title and the review text for each of the training data rows

# 1 observation per reviewer - Few-shot OpenAI

In [22]:

def predict_ratings_few_shot_and_save(data, 
                                      columns_for_training, 
                                      columns_for_prediction, 
                                      user_column_name='reviewerID', 
                                      title_column_name='title', 
                                      asin_column_name='asin', 
                                      rating_column_name='rating',
                                      obs_per_user=None, 
                                      pause_every_n_users=PAUSE_EVERY_N_USERS, 
                                      sleep_time=SLEEP_TIME, 
                                      save_path='few_shot_predictions.csv'):
    results = []
    users = data[user_column_name].unique()

    for idx, user_id in enumerate(users):
        user_data = data[data[user_column_name] == user_id]

        if len(user_data) < 5:
            continue

        user_data = user_data.sample(frac=1, random_state=RANDOM_STATE).reset_index(drop=True)
        
        for test_idx, test_row in user_data.iterrows():
            # Skip the current item being predicted
            train_data = user_data[user_data[asin_column_name] != test_row[asin_column_name]]

            # Select 4 distinct previous ratings
            if len(train_data) >= 4:
                train_data = train_data.head(4)
            else:
                continue  # Skip if there are not enough historical ratings

            prediction_data = {col: test_row[col] for col in columns_for_prediction if col != rating_column_name}
            combined_text = generate_combined_text_for_prediction(columns_for_prediction, *prediction_data.values())

            rating_history_str = '\n'.join([
                '* ' + ' | '.join(f"{col}: {row[col]}" for col in columns_for_training) + f" - Rating: {row[rating_column_name]} stars"
                for _, row in train_data.iterrows()
            ])

            predicted_rating = predict_rating_combined_ChatCompletion(combined_text, rating_history=rating_history_str, approach="few-shot")

            item_id = test_row[asin_column_name]
            actual_rating = test_row[rating_column_name]
            title = test_row[title_column_name]

            results.append([user_id, item_id, title, actual_rating, predicted_rating])

            if obs_per_user and len(results) >= obs_per_user:
                break

        if (idx + 1) % pause_every_n_users == 0:
            print(f"Processed {idx + 1} users. Pausing for {sleep_time} seconds...")
            time.sleep(sleep_time)

    # Save results to CSV
    results_df = pd.DataFrame(results, columns=['user_id', 'item_id', 'title', 'actual_rating', 'predicted_rating'])
    results_df.to_csv(save_path, index=False)
    print("Predictions saved to", save_path)


In [25]:
%%time

predict_ratings_few_shot_and_save(data,
                                      columns_for_training=['Title'],
                                       columns_for_prediction=['Title'],
                                       title_column_name='Title', 
                                       user_column_name='UserID',
                                       asin_column_name='MovieID',
                                       rating_column_name='Rating',
                                       obs_per_user=1,
                                       pause_every_n_users=PAUSE_EVERY_N_USERS,
                                       sleep_time=SLEEP_TIME,
                                       save_path=FEW_SHOT_1_OBS_SAVE_PATH)


Constructed Prompt for few-shot approach:

The prompt:
**********
How will user rate this Title: Pleasantville (1998)? (1 being lowest and 5 being highest) Attention! Just give me back the exact number as a result, and you don't need a lot of text.

Here is user rating history:
* Title: Antz (1998) - Rating: 4 stars
* Title: Dead Poets Society (1989) - Rating: 4 stars
* Title: Sixth Sense, The (1999) - Rating: 4 stars
* Title: Mary Poppins (1964) - Rating: 5 stars

Based on the above information, please predict user's rating for the product: (1 being lowest and 5 being highest, The output should be like: (x stars, xx%), do not explain the reason.)
**********



System Fingerprint: fp_f3efa6edfc

API call response: "4"
Extracted rating: 4.0
Constructed Prompt for few-shot approach:

The prompt:
**********
How will user rate this Title: GoodFellas (1990)? (1 being lowest and 5 being highest) Attention! Just give me back the exact number as a result, and you don't need a lot of text.

Her

In [ ]:
import pandas as pd

# Read the data
data = pd.read_csv(FEW_SHOT_1_OBS_SAVE_PATH)

# Display the original data types
# print("Original Data Types:")
# print(data.dtypes)
# print("\n")

# Attempt to convert ratings to float and add a flag for conversion failure
data['is_rating_float'] = pd.to_numeric(data['predicted_rating'], errors='coerce').notna()

# Filter rows where ratings are not float
non_float_ratings = data[data['is_rating_float'] == False]

# total number of rows with non-float ratings
print(f"Total number of rows with non-float ratings: {len(non_float_ratings)}")

# Display rows with non-float ratings
print("Rows with non-float ratings:")
non_float_ratings.head(3)


In [ ]:
evaluate_model_predictions_rmse_mae(
    data_path=FEW_SHOT_1_OBS_SAVE_PATH,
    num_examples=NUM_EXAMPLES,
    actual_ratings_column='actual_rating',
    predicted_ratings_column='predicted_rating'
)

FileNotFoundError: [Errno 2] No such file or directory: '/Users/tnathu-ai/VSCode/recommender-system/recommender-system-openAI/rec-sys/notebook/../data/ml-1m/output/title_1_test_predictions_few_shot.csv'

# Limitations:

The model might not fully understand the nuanced relationships between products based on titles alone. Additional context or features might be needed for more accurate predictions.
This approach might be computationally expensive and slower than traditional matrix factorization or deep learning-based recommendation models, especially for a large number of users.

# References

+ https://platform.openai.com/docs/api-reference/authentication